# Run GEODYN

In [1]:
%load_ext autoreload
%autoreload 2

from pygeodyn.PYGEODYN import Pygeodyn
from gc import collect as gc_collect

# run_settings = Pygeodyn.print_input(options=False, info=False)

settings_SPIRE= {# Basic input settings
                 'satellite'      :  {'input': 'spire83'}         ,
                 'den_model'      :  {'input': 'jb2008'}          ,
                 'run_type'       :  {'input': 'OrbitPropagation'},
                 'run_specifier'  :  {'input': '_test_infrastruc'},
                 'cd_model'       :  {'input': 'BWDRAG'}          ,
                 'file_string'    :  {'input': 'CD_2p3'}          ,
               # Force Model settings
                  'cd_type'               : {'input':"Fixed_CD"},
                  'cd_value'              : {'input':2.300000},
                  'scaling_factor'        : {'input':False},
                  'cd_adjustment_boolean' : {'input':False },
                  'hours_between_cd_adj'  : {'input':6 },
               # Run
                  'step'           : {'input': 60.},
                  #
#                   'arc'            : {'input':['2018.313',]},
#                   'epoch_start'    : {'input':["2018-11-09 00:00:00"]},
#                   'epoch_stop'     : {'input':["2018-11-10 00:00:00"]},
#                   'arc'            : {'input':['2018.312',]},
#                   'epoch_start'    : {'input':["2018-11-08 00:00:00"]},
#                   'epoch_stop'     : {'input':["2018-11-09 00:00:00"]},
                  'arc'            : {'input':['2018.311',]},
                  'epoch_start'    : {'input':["2018-11-07 00:00:00"]},
                  'epoch_stop'     : {'input':["2018-11-08 00:00:00"]},
        # r_eci   [-5940662.04032,   -2074224.62981,    2733575.86992  ]
        # v_eci  [   -5151.36351,      -5151.36351,      -5151.36351  ]

                  'global_options': {'input':'pso_2018'},
               # Request read on raw outputs
                  'request_data'   : {'input': ['Trajectory_orbfil',
                                                'Density',
                                                'DragFile',
                                                #'Residuals_summary',
                                               ]},
              #end dict
              }

In [2]:
# sat = Pygeodyn(settings_SPIRE, use_file=False)
# # sat = Pygeodyn(settings_icesat, use_file=False)

# sat.run_arcs()
# # obj = sat.getData()

# Check the SLERP function

- The raw spire attitude data represents the rotation: `SBF-->RSW`.  
- The processed EXAT quaternions represent the rotation: `SBF-->J2000`.  

Therefore we cannot compare them 1:1.
Instead, we look at the raw quaternions after the transformation but before the interpolation.

### 'Raw' Spire Quaternions

In [22]:
import pandas as pd
from pygeodyn.satellite_spire import load_attitude_spire
import numpy as np
from pygeodyn.util_dir.quaternions      import quat_trans_SBFtoRSW_to_SBFtoECI
from pygeodyn.util_dir.quaternions      import call_slerp_SpireAtt
from pygeodyn.util_dir.time_systems     import time_gps_to_tdt

from pygeodyn.util_dir.time_systems       import get_leapseconds
from pygeodyn.util_dir.time_systems       import time_gps_to_utc
from pygeodyn.util_dir.coordinate_systems import call_teme2eci


#### OPTIONS: ------------------------------------------------------------------
path_attitude     = "/data/SatDragModelValidation/data/inputs/"\
                   +"sat_spire83/data_Spire/attitude/"\
                   +"20180923_20181209_TaskOrder3Data/"
filename          = "leoAtt_2018-09-23T00-12-00Z.9999999.083.log"
file__AttitudeLog = path_attitude+filename
epoch_startDT = pd.to_datetime(settings_SPIRE['epoch_start']['input'][0],format='%Y-%m-%d %H:%M:%S')
epoch_stopDT  = pd.to_datetime(settings_SPIRE['epoch_stop']['input'][0],format='%Y-%m-%d %H:%M:%S')
one_hour      = pd.to_timedelta(1,'h')
startEpoch    = epoch_startDT  - one_hour  
stopEpoch     = epoch_stopDT   + one_hour
interval      = 10  # seconds
one_hour    = pd.to_timedelta(1,'h')
#### ------------------------------------------------------------------

#### 1. Load the attitude data that corresponds to the entire timeperiod
SpireDF = load_attitude_spire(file__AttitudeLog,
                                startEpoch,
                                stopEpoch)

#### 2. Convert from GPS time to TDT time
SpireDF['tim (tdt)'] = [time_gps_to_tdt(tim, leap_sec=37) 
                                for tim in SpireDF['tim (gps)'] 
                                        ]
### 2.5) Prerequisite transformation for pos and vel
###      from eci-teme-of epoch to eci-j2000 for 

r_j2000_list = []
v_j2000_list = []

for i,val in enumerate(SpireDF['tim (gps)']):
    #### First convert to UTC
    ####   get the leapseconds for time of interest
    dat = get_leapseconds(SpireDF['tim (gps)'][0].year,\
                        SpireDF['tim (gps)'][0].month,\
                        SpireDF['tim (gps)'][0].day)
    date_utc = time_gps_to_utc(SpireDF['tim (gps)'][i], dat)
    #
    year   = date_utc.year
    mon    = date_utc.month
    day    = date_utc.day
    hr     = date_utc.hour
    minute = date_utc.minute
    sec    = date_utc.second

    # position vector earth fixed  ( km )
    r_teme = list(SpireDF['pos (eci)'][i]) 
    v_teme = list(SpireDF['vel (eci)'][i]) 

    r_j2000, v_j2000 = call_teme2eci(r_teme, v_teme, None,\
                                    year, mon, day,        \
                                    hr, minute, sec,       \
                                    calc_accel=False)

    r_j2000_list.append(r_j2000.transpose().squeeze())
    v_j2000_list.append(v_j2000.transpose().squeeze())

#### 3. Perform a coordinate transformation from SBF-->RSW to SBF-->ECI(j2000)
q_SBFtoECI = [quat_trans_SBFtoRSW_to_SBFtoECI(r_j2000_list[i], 
                                              v_j2000_list[i], 
                                            SpireDF['q (sbf)'].iloc[i]) 
                                        for i,val in enumerate(SpireDF['tim (gps)'])]


# Fix the negatives such that no scalar component is negative
SpireDF['q (SBFtoECI)'] = [-1*x if x[3]<0
                                else x
                                for x in q_SBFtoECI]


####  TEST--- Decimate the 10s data to every 15 minutes.
tim_tdt= []
quats  = []
for i,val in enumerate(SpireDF['tim (gps)'][::105].index):
#     print()
    tim_tdt.append(SpireDF['tim (tdt)'].iloc[val])
    quats.append(SpireDF['q (SBFtoECI)'].iloc[val])
    
Spire_15mins = pd.DataFrame(data={"tim (tdt)":tim_tdt,
                                 "q (SBFtoECI)":quats})

# del SpireDF
del tim_tdt, quats
del q_SBFtoECI
del r_j2000_list, v_j2000_list
import gc
gc.collect()

### 4. Interpolate Quaternions to linearly spaced time series
exatt_quats = call_slerp_SpireAtt(Spire_15mins, 
                                startEpoch, 
                                stopEpoch, 
                                interval )
##### Free up some memory:
# del SpireDF['q (sbf)']


# qx =[] 
# qy =[] 
# qz =[] 
# qw =[] 

# for i,val in enumerate(SpireDF['tim (gps)']):
#     qx.append(SpireDF['q (SBFtoECI)'][i][0])
#     qy.append(SpireDF['q (SBFtoECI)'][i][1])
#     qz.append(SpireDF['q (SBFtoECI)'][i][2])
#     qw.append(SpireDF['q (SBFtoECI)'][i][3])
    
    
    
    

In [24]:
del SpireDF['tim (gps)']
del SpireDF['q (sbf)']
del SpireDF['pos (eci)']
del SpireDF['vel (eci)']

### Prep the raw quaternions

In [51]:
qx_raw = []
qy_raw = []
qz_raw = []
qw_raw = []

for i,val in enumerate(SpireDF['q (SBFtoECI)'].index):
    qx_raw.append(SpireDF['q (SBFtoECI)'].iloc[val][0])
    qy_raw.append(SpireDF['q (SBFtoECI)'].iloc[val][1])
    qz_raw.append(SpireDF['q (SBFtoECI)'].iloc[val][2])
    qw_raw.append(SpireDF['q (SBFtoECI)'].iloc[val][3])

In [53]:
# qx_raw

### Prep the Slerpd quaternions

In [54]:
# exatt_quats['tim (tdt)']

qx_slerp = exatt_quats['q (SBFtoECI)'][:,0]
qy_slerp = exatt_quats['q (SBFtoECI)'][:,1]
qz_slerp = exatt_quats['q (SBFtoECI)'][:,2]
qw_slerp = exatt_quats['q (SBFtoECI)'][:,3]

In [58]:
qx_decim = []
qy_decim = []
qz_decim = []
qw_decim = []

for i,val in enumerate(Spire_15mins['q (SBFtoECI)'].index):
    qx_decim.append(Spire_15mins['q (SBFtoECI)'].iloc[val][0])
    qy_decim.append(Spire_15mins['q (SBFtoECI)'].iloc[val][1])
    qz_decim.append(Spire_15mins['q (SBFtoECI)'].iloc[val][2])
    qw_decim.append(Spire_15mins['q (SBFtoECI)'].iloc[val][3])


In [55]:
### Slerpd Quaternions from exat file

# file_slerp_exattxt = '/data/SatDragModelValidation/data/inputs/'\
#                     + 'sat_spire83/external_attitude/EXAT01.'   \
#                     + settings_SPIRE['arc']['input'][0]         \
#                     + '_check.txt'

# slerp_quats = pd.read_csv(file_slerp_exattxt, 
#             skiprows = 4, 
# #             nrows=1,           
#             sep = ',',
#             dtype=str,
#             names = ['date_gps',
#                      'qx',
#                      'qy',
#                      'qz',
#                      'qw',
#                     ],)
# slerp_quats.head()


In [60]:
%load_ext autoreload
%autoreload 2
import plotly.graph_objects as go
from plotly.offline import plot, iplot
from plotly.subplots import make_subplots
import plotly.express as px

config = dict({
                'displayModeBar': True,
                'responsive': False,
                'staticPlot': True,
                'displaylogo': False,
                'showTips': False,
                })


fig = make_subplots(rows=4, cols=1)

##### "Raw" Quaternions 
fig.add_trace(go.Scattergl(
            x=pd.to_datetime(SpireDF['tim (tdt)']),
            y=qx_raw,
                mode='markers',
                opacity=1,
                marker=dict(size=3.5, color = 'grey'),
                showlegend=False),
                secondary_y=False, row=1, col=1,)
fig.add_trace(go.Scattergl(
            x=pd.to_datetime(SpireDF['tim (tdt)']),
            y=qy_raw,
                mode='markers',
                opacity=1,
                marker=dict(size=3.5, color = 'grey'),
                showlegend=False),
                secondary_y=False, row=2, col=1,)
fig.add_trace(go.Scattergl(
            x=pd.to_datetime(SpireDF['tim (tdt)']),
            y=qz_raw,
                mode='markers',
                opacity=1,
                marker=dict(size=3.5, color = 'grey'),     
                showlegend=False),
                secondary_y=False, row=3, col=1,)
fig.add_trace(go.Scattergl(
            x=pd.to_datetime(SpireDF['tim (tdt)']),
            y=qw_raw,
                mode='markers',
                opacity=1,
                marker=dict(size=3.5, color = 'grey'),     
                showlegend=False),
                secondary_y=False, row=4, col=1,)

#####-------------------------------------------------------------------------
##### SLERPd quaternions
fig.add_trace(go.Scattergl(
            x=exatt_quats['tim (tdt)'],
            y=qx_slerp,
                mode='markers',
                opacity=1,
                marker=dict(size=2.5, color = 'black'),
                showlegend=False),
                secondary_y=False, row=1, col=1,)

fig.add_trace(go.Scattergl(
            x=exatt_quats['tim (tdt)'],
            y=qy_slerp,
                mode='markers',
                opacity=1,
                marker=dict(size=2.5, color = 'black'),
                showlegend=False),
                secondary_y=False, row=2, col=1,)

fig.add_trace(go.Scattergl(
            x=exatt_quats['tim (tdt)'],
            y=qz_slerp,
                mode='markers',
                opacity=1,
                marker=dict(size=2.5, color = 'black'),     
                showlegend=False),
                secondary_y=False, row=3, col=1,)

fig.add_trace(go.Scattergl(
            x=exatt_quats['tim (tdt)'],
            y=qw_slerp,
                mode='markers',
                opacity=1,
                marker=dict(size=2.5, color = 'black'),     
                showlegend=False),
                secondary_y=False, row=4, col=1,)
#####-------------------------------------------------------------------------
##### SLERPd decimated
fig.add_trace(go.Scattergl(
            x=Spire_15mins['tim (tdt)'],
            y=qx_decim,
                mode='markers',
                opacity=1,
                marker=dict(size=2.5, color = 'red'),
                showlegend=False),
                secondary_y=False, row=1, col=1,)

fig.add_trace(go.Scattergl(
            x=Spire_15mins['tim (tdt)'],
            y=qy_decim,
                mode='markers',
                opacity=1,
                marker=dict(size=2.5, color = 'red'),
                showlegend=False),
                secondary_y=False, row=2, col=1,)

fig.add_trace(go.Scattergl(
            x=Spire_15mins['tim (tdt)'],
            y=qz_decim,
                mode='markers',
                opacity=1,
                marker=dict(size=2.5, color = 'red'),     
                showlegend=False),
                secondary_y=False, row=3, col=1,)

fig.add_trace(go.Scattergl(
            x=Spire_15mins['tim (tdt)'],
            y=qw_decim,
                mode='markers',
                opacity=1,
                marker=dict(size=2.5, color = 'red'),     
                showlegend=False),
                secondary_y=False, row=4, col=1,)






fig.update_yaxes(title="qx", row=1, col=1)
fig.update_yaxes(title="qy", row=2, col=1)
fig.update_yaxes(title="qz", row=3, col=1)
fig.update_yaxes(title="qw", row=4, col=1)

fig.update_xaxes( #title="",
     range=[pd.to_datetime( "181107-000000", format='%y%m%d-%H%M%S'),
            pd.to_datetime( "181108-010000", format='%y%m%d-%H%M%S')],
#                  row=4, col=1,
                )

fig.update_layout(title="Check SLERP Interpolation (black=Slerpd, grey='Raw')",
        width=800,height=900,
                )


The autoreload extension is already loaded. To reload it, use:
  %reload_ext autoreload
